In [1]:
import base64
import io
import pickle
import numpy as np
import torch
from ray import tune   # we will use ray tune for the optimization
import packaging.version
%matplotlib inline
if torch.cuda.is_available():
    torch_device = 'cuda'
    float_dtype = np.float32
    torch.set_default_tensor_type(torch.cuda.FloatTensor)
else:
    torch_device = 'cpu'
    float_dtype = np.float64
    torch.set_default_tensor_type(torch.FloatTensor)

TORCH VERSION: 1.8.0
TORCH DEVICE: cuda


In [2]:
def torch_mod(x):
    return torch.remainder(x, 2*np.pi)
def torch_wrap(x):
    return torch_mod(x+np.pi) - np.pi
def grab(var):
    return var.detach().cpu().numpy()

In [3]:
class SimpleNormal:  # The prior distribution
    def __init__(self, loc, var):
        self.dist = torch.distributions.normal.Normal(
            torch.flatten(loc), torch.flatten(var))
        self.shape = loc.shape
    def log_prob(self, x):
        logp = self.dist.log_prob(x.reshape(x.shape[0], -1))
        return torch.sum(logp, dim=1)
    def sample_n(self, batch_size):
        x = self.dist.sample((batch_size,))
        return x.reshape(batch_size, *self.shape)

In [4]:
class ScalarPhi4Action: # The action for phi^4 2D scalar field theory
    def __init__(self, M2, lam):
        self.M2 = M2
        self.lam = lam
    def __call__(self, cfgs):
        # potential term
        action_density = self.M2*cfgs**2 + self.lam*cfgs**4 
        Nd = len(cfgs.shape)-1
        dims = range(1,Nd+1)
        for mu in dims:
            action_density += 2*cfgs**2
            action_density -= cfgs*torch.roll(cfgs, -1, mu)
            action_density -= cfgs*torch.roll(cfgs, 1, mu)
        return torch.sum(action_density, dim=tuple(dims))

In [5]:
def make_checker_mask(shape, parity):  # checkermark pattern
    checker = torch.ones(shape, dtype=torch.uint8) - parity
    checker[::2, ::2] = parity
    checker[1::2, 1::2] = parity
    return checker.to(torch_device)

In [6]:
class AffineCoupling(torch.nn.Module):  # Affine coupling layer
    def __init__(self, net, *, mask_shape, mask_parity):
        super().__init__()
        self.mask = make_checker_mask(mask_shape, mask_parity)
        self.net = net.to(torch_device)
    def forward(self, x):
        x_frozen = self.mask * x
        x_active = (1 - self.mask) * x
        net_out = self.net(x_frozen.unsqueeze(1))
        s, t = net_out[:,0], net_out[:,1]
        fx = (1 - self.mask) * t + x_active * torch.exp(s) + x_frozen
        axes = range(1,len(s.size()))
        logJ = torch.sum((1 - self.mask) * s, dim=tuple(axes))
        return fx, logJ
    def reverse(self, fx):
        fx_frozen = self.mask * fx
        fx_active = (1 - self.mask) * fx
        net_out = self.net(fx_frozen.unsqueeze(1))
        s, t = net_out[:,0], net_out[:,1]
        x = (fx_active - (1 - self.mask) * t) * torch.exp(-s) + fx_frozen
        axes = range(1,len(s.size()))
        logJ = torch.sum((1 - self.mask)*(-s), dim=tuple(axes))
        return x, logJ

In [7]:
def make_conv_net(*, hidden_sizes, kernel_size, in_channels, out_channels, use_final_tanh): # CCN
    sizes = [in_channels] + hidden_sizes + [out_channels]
    padding_size = (kernel_size // 2)
    net = []
    for i in range(len(sizes) - 1):
        net.append(torch.nn.Conv2d(
            sizes[i], sizes[i+1], kernel_size, padding=padding_size, 
            stride=1, padding_mode='circular'))
        if i != len(sizes) - 2:
            net.append(torch.nn.LeakyReLU())
        else:
            if use_final_tanh:
                net.append(torch.nn.Tanh())
    return torch.nn.Sequential(*net)

In [8]:
def objective(n_layers, hidden_sizes, kernel_size, batch_size, lr): # Assemble the network
    layers = []
    for i in range(n_layers):  # stack the layers
        parity = i % 2
        net = make_conv_net(
            in_channels=1, out_channels=2, hidden_sizes=hidden_sizes,
            kernel_size=kernel_size, use_final_tanh=True)
        coupling = AffineCoupling(net, mask_shape=lattice_shape, mask_parity=parity)
        layers.append(coupling)
    layers =  torch.nn.ModuleList(layers)
    optimizer = torch.optim.Adam(layers.parameters(), lr = lr) # set Adam optimizer
    optimizer.zero_grad()
    x = prior.sample_n(batch_size)
    logq = prior.log_prob(x)
    for layer in layers:
        x, logJ = layer.forward(x)
        logq = logq - logJ
    logp = -phi4_action(x)
    loss = (logq - logp).mean()
    loss.backward()
    optimizer.step()
    return loss.item() # Return loss

def trainable(config):
    n_layers = config["n_layers"]
    hidden_sizes = [config["hidden_size"],config["hidden_size"]]
    kernel_size = config["kernel_size"]
    batch_size = config["batch_size"]
    lr = config["lr"]
    for era in range(N_era):
        for epoch in range(N_epoch):
            intermediate_score = objective(n_layers, hidden_sizes, kernel_size, batch_size, lr)
            tune.report(mean_loss=intermediate_score) 
            

In [9]:
# Parameters
L=6
lattice_shape = (L,L)
M2 = -4.0
lam = 8.0
N_era = 25
N_epoch = 100
phi4_action = ScalarPhi4Action(M2=M2, lam=lam)
prior = SimpleNormal(torch.zeros(lattice_shape), torch.ones(lattice_shape))
# Initialize dictionary for parameter ranges to optimize
config={"n_layers": tune.sample_from(lambda _: 2**np.random.randint(2, 9)),
        "hidden_size": tune.randint(2,27),
        "kernel_size": tune.choice([3,5]),
        "lr": tune.uniform(0.0001,0.01),
        "batch_size": tune.sample_from(lambda _: 2**np.random.randint(2, 11))}


In [11]:
# example of optimization
analysis = tune.run(trainable, config=config, num_samples=1000,resources_per_trial={"gpu": 1})


(pid=23392) torch.float32
Result for trainable_dace8_00000:
  date: 2021-04-10_19-28-01
  done: false
  experiment_id: 89b1edb4866f4ae3b48d91a9ed77a608
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 230.5252685546875
  neg_mean_loss: -230.5252685546875
  node_ip: 10.128.0.2
  pid: 23392
  time_since_restore: 1.3574631214141846
  time_this_iter_s: 1.3574631214141846
  time_total_s: 1.3574631214141846
  timestamp: 1618082881
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00000
  
Result for trainable_dace8_00000:
  date: 2021-04-10_19-28-01
  done: true
  experiment_id: 89b1edb4866f4ae3b48d91a9ed77a608
  experiment_tag: 0_batch_size=256,hidden_size=26,kernel_size=3,lr=0.0041258,n_layers=64
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 230.5252685546875
  neg_mean_loss: -230.5252685546875
  node_ip: 10.128.0.2
  pid: 23392
  time_since_restore: 1.3574631214141846
  time_this_iter_s: 1.3574631214141846
  time_total_s: 1.357463121414184

Result for trainable_dace8_00001:
  date: 2021-04-10_19-28-09
  done: true
  experiment_id: 25725c05fc394551a5c9d93265a98953
  experiment_tag: 1_batch_size=256,hidden_size=20,kernel_size=3,lr=0.0085964,n_layers=256
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 6.048835494532634e+34
  neg_mean_loss: -6.048835494532634e+34
  node_ip: 10.128.0.2
  pid: 23394
  time_since_restore: 4.559616565704346
  time_this_iter_s: 4.559616565704346
  time_total_s: 4.559616565704346
  timestamp: 1618082889
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00001
  
(pid=23395) torch.float32
Result for trainable_dace8_00002:
  date: 2021-04-10_19-28-14
  done: false
  experiment_id: e52a5f229ca141c88c13fdd85fa26743
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 6158.4716796875
  neg_mean_loss: -6158.4716796875
  node_ip: 10.128.0.2
  pid: 23395
  time_since_restore: 2.4220633506774902
  time_this_iter_s: 2.4220633506774902
  time_total_s: 2.4220633506774

Result for trainable_dace8_00002:
  date: 2021-04-10_19-28-14
  done: true
  experiment_id: e52a5f229ca141c88c13fdd85fa26743
  experiment_tag: 2_batch_size=16,hidden_size=23,kernel_size=3,lr=0.0041995,n_layers=256
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 6158.4716796875
  neg_mean_loss: -6158.4716796875
  node_ip: 10.128.0.2
  pid: 23395
  time_since_restore: 2.4220633506774902
  time_this_iter_s: 2.4220633506774902
  time_total_s: 2.4220633506774902
  timestamp: 1618082894
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00002
  
(pid=23393) torch.float32
Result for trainable_dace8_00003:
  date: 2021-04-10_19-28-17
  done: false
  experiment_id: 62ddee88aac24634a6ebea46e28baf8e
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 1043.1455078125
  neg_mean_loss: -1043.1455078125
  node_ip: 10.128.0.2
  pid: 23393
  time_since_restore: 0.32869529724121094
  time_this_iter_s: 0.32869529724121094
  time_total_s: 0.32869529724121094
  t

Result for trainable_dace8_00004:
  date: 2021-04-10_19-28-21
  done: true
  experiment_id: 1c5ca8a9b3ca4a45b6a923274158411a
  experiment_tag: 4_batch_size=8,hidden_size=10,kernel_size=5,lr=0.0096174,n_layers=128
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 15881.9296875
  neg_mean_loss: -15881.9296875
  node_ip: 10.128.0.2
  pid: 23390
  time_since_restore: 1.222393274307251
  time_this_iter_s: 1.222393274307251
  time_total_s: 1.222393274307251
  timestamp: 1618082901
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00004
  
(pid=23391) torch.float32
Result for trainable_dace8_00005:
  date: 2021-04-10_19-28-25
  done: false
  experiment_id: cb3b709cd4c343d8ac675e6f2bec2968
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 1077670.25
  neg_mean_loss: -1077670.25
  node_ip: 10.128.0.2
  pid: 23391
  time_since_restore: 1.3881731033325195
  time_this_iter_s: 1.3881731033325195
  time_total_s: 1.3881731033325195
  timestamp: 1618082905


Result for trainable_dace8_00006:
  date: 2021-04-10_19-28-29
  done: true
  experiment_id: 687cf3561d574048bce1fb5945b96695
  experiment_tag: 6_batch_size=512,hidden_size=15,kernel_size=5,lr=0.0069131,n_layers=16
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 4724.96533203125
  neg_mean_loss: -4724.96533203125
  node_ip: 10.128.0.2
  pid: 23652
  time_since_restore: 0.5902409553527832
  time_this_iter_s: 0.5902409553527832
  time_total_s: 0.5902409553527832
  timestamp: 1618082909
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00006
  
(pid=23675) torch.float32
Result for trainable_dace8_00007:
  date: 2021-04-10_19-28-32
  done: false
  experiment_id: 4995fcea38e64b9581468239e0fe13cb
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 1135.0390625
  neg_mean_loss: -1135.0390625
  node_ip: 10.128.0.2
  pid: 23675
  time_since_restore: 0.3065159320831299
  time_this_iter_s: 0.3065159320831299
  time_total_s: 0.3065159320831299
  timestam

...

Result for trainable_dace8_00992:
  date: 2021-04-10_20-38-26
  done: true
  experiment_id: 8bd1501c46b043569acfa45d6a870293
  experiment_tag: 992_batch_size=512,hidden_size=10,kernel_size=3,lr=0.0015243,n_layers=128
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 100174348288.0
  neg_mean_loss: -100174348288.0
  node_ip: 10.128.0.2
  pid: 16508
  time_since_restore: 2.6370387077331543
  time_this_iter_s: 2.6370387077331543
  time_total_s: 2.6370387077331543
  timestamp: 1618087106
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00992
  
Result for trainable_dace8_00993:
  date: 2021-04-10_20-38-30
  done: false
  experiment_id: 0a77b4ebd89840c58d6e2b060f8ba9ff
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 10339174.0
  neg_mean_loss: -10339174.0
  node_ip: 10.128.0.2
  pid: 16531
  time_since_restore: 1.3708288669586182
  time_this_iter_s: 1.3708288669586182
  time_total_s: 1.3708288669586182
  timestamp: 1618087110
  timesteps_since

Result for trainable_dace8_00994:
  date: 2021-04-10_20-38-37
  done: true
  experiment_id: 63e401d82617402884a39aad1927c9e3
  experiment_tag: 994_batch_size=1024,hidden_size=24,kernel_size=3,lr=0.0015992,n_layers=128
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 2026.4635009765625
  neg_mean_loss: -2026.4635009765625
  node_ip: 10.128.0.2
  pid: 16560
  time_since_restore: 3.1966490745544434
  time_this_iter_s: 3.1966490745544434
  time_total_s: 3.1966490745544434
  timestamp: 1618087117
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00994
  
Result for trainable_dace8_00995:
  date: 2021-04-10_20-38-40
  done: false
  experiment_id: 1f459b8e5fbe4a2eba812feec99a8472
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 5592.9013671875
  neg_mean_loss: -5592.9013671875
  node_ip: 10.128.0.2
  pid: 16583
  time_since_restore: 0.4006624221801758
  time_this_iter_s: 0.4006624221801758
  time_total_s: 0.4006624221801758
  timestamp: 161808712

Result for trainable_dace8_00996:
  date: 2021-04-10_20-38-44
  done: true
  experiment_id: b47ace0073de455cbea857ea7946de74
  experiment_tag: 996_batch_size=4,hidden_size=15,kernel_size=3,lr=0.001721,n_layers=64
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 2712.39208984375
  neg_mean_loss: -2712.39208984375
  node_ip: 10.128.0.2
  pid: 16612
  time_since_restore: 0.7803668975830078
  time_this_iter_s: 0.7803668975830078
  time_total_s: 0.7803668975830078
  timestamp: 1618087124
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00996
  
Result for trainable_dace8_00997:
  date: 2021-04-10_20-38-48
  done: false
  experiment_id: f908e60787f24de28ea0af8427225d45
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 4435.90478515625
  neg_mean_loss: -4435.90478515625
  node_ip: 10.128.0.2
  pid: 16636
  time_since_restore: 0.5326497554779053
  time_this_iter_s: 0.5326497554779053
  time_total_s: 0.5326497554779053
  timestamp: 1618087128
  tim

Result for trainable_dace8_00998:
  date: 2021-04-10_20-38-54
  done: true
  experiment_id: e851ebe0b9b7426aa52a3ccea1961ef7
  experiment_tag: 998_batch_size=1024,hidden_size=22,kernel_size=3,lr=0.0061848,n_layers=128
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 2092.775390625
  neg_mean_loss: -2092.775390625
  node_ip: 10.128.0.2
  pid: 16660
  time_since_restore: 3.127462863922119
  time_this_iter_s: 3.127462863922119
  time_total_s: 3.127462863922119
  timestamp: 1618087134
  timesteps_since_restore: 0
  training_iteration: 1
  trial_id: dace8_00998
  
Result for trainable_dace8_00999:
  date: 2021-04-10_20-38-59
  done: false
  experiment_id: b76a175d794e4003a0a8161717edf5c4
  hostname: mv6862
  iterations_since_restore: 1
  mean_loss: 295645632.0
  neg_mean_loss: -295645632.0
  node_ip: 10.128.0.2
  pid: 16689
  time_since_restore: 1.270467758178711
  time_this_iter_s: 1.270467758178711
  time_total_s: 1.270467758178711
  timestamp: 1618087139
  timesteps_since_re

2021-04-10 20:38:59,675	INFO tune.py:450 -- Total run time: 4262.20 seconds (4261.85 seconds for the tuning loop).


In [12]:
print("Best config: ", analysis.get_best_config(
    metric="mean_loss", mode="min"))

Best config:  {'n_layers': 128, 'hidden_size': 2, 'kernel_size': 3, 'lr': 0.0028249231944095414, 'batch_size': 128}
